In [1]:
!pip install arcgis folium requests

In [2]:
import requests
import folium
from folium import FeatureGroup, LayerControl, GeoJson, Popup
from folium.plugins import MarkerCluster
from arcgis.gis import GIS
from IPython.display import display

In [3]:
gis = GIS()

In [4]:
map_center = [38.5976, -80.4549]
folium_map = folium.Map(location=map_center, zoom_start=7)

In [5]:
criticalinfra = gis.content.get('3d92487b911f4c3ab8322a8ead078b6e')

if not criticalinfra:
    raise Exception("Failed to fetch the ArcGIS content. Please check the item ID and access permissions.")

layer_names = {} 

for i, layer in enumerate(criticalinfra.layers):
    layer_names[i] = layer.properties.name
    print(f"Layer {i}: {layer.properties.name}")

layer_indices = range(len(criticalinfra.layers))

colors = [
    'red', 'blue', 'green', 'purple', 'orange', 'darkred',
    'lightred', 'beige', 'darkblue', 'darkgreen', 'cadetblue',
    'darkpurple', 'white', 'pink', 'lightblue'
]


Layer 0: 911 Centers
Layer 1: Correctional Facilities
Layer 2: EMS Stations 
Layer 3: Fire Departments
Layer 4: Health Departments
Layer 5: Higher Education Locations
Layer 6: Hospitals
Layer 7: Nursing Homes
Layer 8: OES Centers
Layer 9: Police Departments
Layer 10: Primary Care Centers
Layer 11: Private Schools
Layer 12: Public Libraries
Layer 13: Public Schools
Layer 14: Counties


In [1]:
for idx in layer_indices:
    feature_service_url = f"https://services3.arcgis.com/XQfPLTVDElDOMEad/arcgis/rest/services/WVDHSEM_Critical_Infrastructure_Map/FeatureServer/{idx}/query"

    params = {
        "where": "1=1",
        "outFields": "*",
        "returnGeometry": "true",
        "f": "geojson"
    }

    response = requests.get(feature_service_url, params=params)
    
    geojson_data = response.json()
    
    for feature in geojson_data.get('features', []):
        properties = feature.get('properties', {})
        properties['FACILITY'] = properties.get('FACILITY', 'Unknown Facility')
        properties['ADDRESS'] = properties.get('ADDRESS', 'Unknown Address')
        properties['CITY'] = properties.get('CITY', 'Unknown City')

    filtered_features = [
        feature for feature in geojson_data.get('features', [])
        if feature.get('geometry') and feature['geometry'].get('type') != 'GeometryCollection'
    ]

    geojson_data['features'] = filtered_features
    print(f"Layer {idx} has {len(geojson_data.get('features', []))} features after filtering.")

    
    if not geojson_data['features']:
        print(f"Layer {idx} has no valid features after filtering. Skipping.")
        continue

    layer_name = layer_names.get(idx, f"Layer {idx}")

    color = colors[idx % len(colors)]

    feature_group = FeatureGroup(name=layer_name)
    
    try:
        point_features = []
        non_point_features = []
        
        for feature in geojson_data.get('features', []):
            geometry = feature.get('geometry', {})
            geom_type = geometry.get('type', None)
            
            if geom_type == 'Point':
                point_features.append(feature)
            #else:
                #non_point_features.append(feature)
        
        #non_point_geojson = {
            #"type": "FeatureCollection",
            #"features": non_point_features
        #}
        

        for feature in point_features:
            properties = feature.get('properties', {})
            geometry = feature.get('geometry', {})
            coordinates = geometry.get('coordinates', [None, None])
            
            if not coordinates or None in coordinates:
                continue
            
            lat, lon = coordinates[1], coordinates[0]
            
            popup_text = f"""
            <b>Facility:</b> {properties.get('FACILITY', 'Unknown')}<br>
            <b>Address:</b> {properties.get('ADDRESS', 'Unknown')}<br>
            <b>City:</b> {properties.get('CITY', 'Unknown')}
            """
    
            folium.CircleMarker(
                location=[lat, lon],
                radius=5,  # Adjust as needed
                color=color,
                fill=True,
                fill_color=color,
                fill_opacity=0.7,
                popup=folium.Popup(popup_text)
            ).add_to(feature_group)
            
    except Exception as e:
        print(f"Error adding GeoJson to layer {idx}: {e}")
        continue  

    feature_group.add_to(folium_map)

NameError: name 'layer_indices' is not defined

In [7]:
arcgis_tile_url_1 = "https://tiles.arcgis.com/tiles/C8EMgrsFcRFL6LrL/arcgis/rest/services/nrmMonTemp/MapServer/tile/{z}/{y}/{x}"
arcgis_tile_url_2 = "https://tiles.arcgis.com/tiles/C8EMgrsFcRFL6LrL/arcgis/rest/services/nrmMonPrecip/MapServer/tile/{z}/{y}/{x}"

folium.TileLayer(
    arcgis_tile_url_1,
    name="Monthly Normal Temperatures",
    attr="ArcGIS",
    overlay=True, 
    control=True,
    show=True    
).add_to(folium_map)

folium.TileLayer(
    arcgis_tile_url_2,
    name="Monthly Normal Precipitation",
    attr="ArcGIS",
    overlay=True,
    control=True,
    show=False     
).add_to(folium_map)

folium.LayerControl().add_to(folium_map)

folium_map